In [1]:
import numpy as np
import pandas as pd
from scipy.stats import norm
np.set_printoptions(suppress=True)
import csv
from numpy import nan
import matplotlib.pyplot as plt
import statsmodels.api as sm
from scipy.linalg import inv
from numpy import cumsum
import openpyxl
import xlrd
#import xlwt
from scipy import stats
from sklearn.decomposition import PCA
import statsmodels.api as sm
from scipy.stats import zscore
import statsmodels.api as sm
import numpy as np
import pandas as pd
from statsmodels.regression.linear_model import OLS
#from statsmodels.api import ols
import statsmodels.formula.api as smf
import pdb
import scipy.stats
from statsmodels.api import OLS
from sklearn.preprocessing import StandardScaler
import random
from openpyxl import load_workbook
from statsmodels.api import OLS
from statsmodels.tools.tools import add_constant



from sklearn.linear_model import LinearRegression


import sys
import warnings
if not sys.warnoptions:
    warnings.simplefilter("ignore")

    
N = norm.cdf
ln = np.log
e = np.exp
sqrt = np.sqrt

In [2]:
dataset = pd.read_excel("Returns_short_interest_data.xlsx")
datasheet = "GW variables"
xls = pd.ExcelFile("Returns_short_interest_data.xlsx")
R_SP500 = pd.read_excel("Returns_short_interest_data.xlsx", sheet_name=0, usecols="Q")
R_SP500 = R_SP500[1224:1728]
R_SP500 = R_SP500.values
r= np.log(1+R_SP500)


In [3]:

GW = np.load('Program_generate_GW1_predictors.npy')
log_DP = GW[:, 0]
GW_adjust = GW.copy()
GW_adjust[:, 6:9] = -GW[:, 6:9]
GW_adjust[:, 11:13]= -GW[:,13:15]
GW_standardize = stats.zscore(GW_adjust, axis=0, ddof=1)
#r=log(1+R_SP500);




In [4]:
X = GW_standardize
X = np.delete(X, [3, 10], axis=1)
pca = PCA(n_components=3)
PC_GW = pca.fit_transform(X)
PC_GW = stats.zscore(PC_GW, axis=0, ddof=1)

input_file = 'Returns_short_interest_data.xlsx'
input_sheet = 'Short interest'

EWSI = pd.read_excel(input_file, sheet_name=input_sheet, usecols="B")
EWSI = EWSI.values[0:505]

log_EWSI = np.log(EWSI)

# Compute log(EWSI) deviation from linear trend
X_linear = np.column_stack((np.ones(len(log_EWSI)), np.arange(len(log_EWSI))))

model_linear = sm.OLS(log_EWSI, X_linear)
results_linear = model_linear.fit()
SII = zscore(results_linear.resid, axis=0, ddof=1).reshape(-1,1)

# Estimate predictive regression for log return based on SII
T = len(r)
#X_linear_2 = np.column_stack((np.ones(len(log_EWSI)-1), np.arange(len(log_EWSI)-1)))
X_predictive = X_predictive = sm.add_constant(SII[:-1]) 
model_predictive = sm.OLS(r[1:]*100, X_predictive)
PR_results = model_predictive.fit(cov_type='HAC', cov_kwds={'maxlags':1})
beta_hat = [PR_results.params[1], PR_results.tvalues[1]]


In [5]:
beta_hat= np.array(beta_hat).reshape(-1,1)
beta_hat = beta_hat.T

In [6]:
rho_hat = 1 / (1 + np.exp(np.mean(log_DP)))
T, GW_cols = len(log_DP), GW.shape[1]

# Create dataframes filled with NaNs
E_hat_r = pd.DataFrame(np.nan, index=np.arange(T-1), columns=np.arange(GW_cols+1))
eta_hat_DR = pd.DataFrame(np.nan, index=np.arange(T-1), columns=np.arange(GW_cols+1))
eta_hat_CF = pd.DataFrame(np.nan, index=np.arange(T-1), columns=np.arange(GW_cols+1))

beta_hat_E_hat_r = pd.DataFrame(np.nan, index=np.arange(GW_cols+1), columns=np.arange(2))
beta_hat_CF = pd.DataFrame(np.nan, index=np.arange(GW_cols+1), columns=np.arange(2))
beta_hat_DR = pd.DataFrame(np.nan, index=np.arange(GW_cols+1), columns=np.arange(2))


In [7]:


for i in range(GW_cols + 1):
    # Endogenous variables for VAR
    if i == 0:
        Y_i = np.column_stack((r, GW[:, 0]))
    elif i > 0 and i < GW_cols:
        Y_i = np.column_stack((r, GW[:, 0], GW[:, i]))
    elif i == GW_cols:
        Y_i = np.column_stack((r, GW[:, 0], PC_GW))

    Y_i_dev = Y_i - np.mean(Y_i, axis=0)
    
    A_hat_i = np.empty((Y_i.shape[1], Y_i.shape[1]))  
    A_hat_i[:] = np.NaN  # VAR slope parameters

    epsilon_hat_i = np.empty((Y_i_dev.shape[0] - 1, Y_i.shape[1]))
    epsilon_hat_i[:] = np.NaN  # VAR shocks


    for j in range(Y_i.shape[1]):
        X = Y_i_dev[:-1, :]  # Adjusted here
        y = Y_i_dev[1:, j]  # Adjusted here
        model = sm.OLS(y, X)
        results_i_j = model.fit()

        if j == 0:
            E_hat_r_i = results_i_j.fittedvalues
            E_hat_r.loc[:, i] = E_hat_r_i

        A_hat_i[j, :] = results_i_j.params
        epsilon_hat_i[:, j] = results_i_j.resid
        
    rho_hat_inv = np.linalg.inv(np.eye(Y_i.shape[1]) - rho_hat * A_hat_i)
    e1_i = np.concatenate(([1], np.zeros(Y_i.shape[1] - 1)))
    eta_hat_i = np.dot(e1_i, epsilon_hat_i.T)
    eta_hat_DR_i = np.dot(e1_i, rho_hat * A_hat_i.dot(rho_hat_inv).dot(epsilon_hat_i.T))
    eta_hat_CF_i = eta_hat_i + eta_hat_DR_i
    
    eta_hat_DR.loc[:, i] = 100 * eta_hat_DR_i
    eta_hat_CF.loc[:, i] = 100 * eta_hat_CF_i

    # Predictive regressions based on SII
    X_pred = sm.add_constant(SII[:-1])
    y_pred = 100 * (E_hat_r.values[:, i] + np.mean(r))

    model = sm.OLS(y_pred, X_pred)
    results_E_hat_r_i = model.fit(cov_type='HAC', cov_kwds={'maxlags': 1})
    
    beta_hat_E_hat_r.loc[i, :] = [results_E_hat_r_i.params[1], results_E_hat_r_i.tvalues[1]]

    y_pred = 100 * eta_hat_DR_i
    model = sm.OLS(y_pred, SII[:-1])
    results_DR_i = model.fit(cov_type='HAC', cov_kwds={'maxlags': 1})
    
    beta_hat_DR.loc[i, :] = [results_DR_i.params[0], results_DR_i.tvalues[0]]

    y_pred = 100 * eta_hat_CF_i
    model = sm.OLS(y_pred, SII[:-1])
    results_CF_i = model.fit(cov_type='HAC', cov_kwds={'maxlags': 1})

    beta_hat_CF.loc[i, :] = [results_CF_i.params[0], results_CF_i.tvalues[0]]
    
    #results_DR_i = nwest(100 * eta_hat_DR_i, SII[:-1], 1)
    #beta_hat_DR.loc[i, :] = [results_DR_i.params, results_DR_i.tvalues]
    
    #results_CF_i = nwest(100 * eta_hat_CF_i, SII[:-1], 1)
    #beta_hat_CF.loc[i, :] = [results_CF_i.params, results_CF_i.tvalues]


In [8]:
# Write results to excel file 
output_file = 'Returns_short_interest_results.xlsx'
output_sheet = 'VAR decomposition'

with pd.ExcelWriter(output_file, engine='openpyxl', mode='a',if_sheet_exists='overlay') as writer:
    pd.DataFrame(beta_hat).to_excel(writer, sheet_name=output_sheet, startrow=19, startcol=12, header=False, index=False)
    pd.DataFrame(beta_hat_E_hat_r).to_excel(writer, sheet_name=output_sheet, startrow=3, startcol=1, header=False, index=False)
    pd.DataFrame(beta_hat_CF).to_excel(writer, sheet_name=output_sheet, startrow=3, startcol=4, header=False, index=False)
    pd.DataFrame(beta_hat_DR).to_excel(writer, sheet_name=output_sheet, startrow=3, startcol=7, header=False, index=False)

In [9]:
## Period 1973:01-2007:12

dataset = pd.read_excel("Returns_short_interest_data.xlsx")
datasheet = "GW variables"
xls = pd.ExcelFile("Returns_short_interest_data.xlsx")
R_SP500 = pd.read_excel("Returns_short_interest_data.xlsx", sheet_name=0, usecols="Q")
R_SP500 = R_SP500[1224:1644]
R_SP500 = R_SP500.values
r= np.log(1+R_SP500)

In [10]:
GW = np.load('Program_generate_GW1_predictors.npy')
log_DP = GW[:-84, 0]
GW_adjust = GW.copy()
GW_adjust[:, 6:9] = -GW[:, 6:9]
GW_adjust[:, 11:13]= -GW[:,13:15]
GW_adjust= GW_adjust[:-84]
GW_standardize = stats.zscore(GW_adjust, axis=0, ddof=1)
#r=log(1+R_SP500);

In [11]:
X = GW_standardize
X = np.delete(X, [3, 10], axis=1)
pca = PCA(n_components=3)
PC_GW = pca.fit_transform(X)
PC_GW = stats.zscore(PC_GW, axis=0, ddof=1)

input_file = 'Returns_short_interest_data.xlsx'
input_sheet = 'Short interest'

EWSI = pd.read_excel(input_file, sheet_name=input_sheet, usecols="B")
EWSI = EWSI.values[0:420]

log_EWSI = np.log(EWSI)

# Compute log(EWSI) deviation from linear trend
X_linear = np.column_stack((np.ones(len(log_EWSI)), np.arange(len(log_EWSI))))

model_linear = sm.OLS(log_EWSI, X_linear)
results_linear = model_linear.fit()
SII = zscore(results_linear.resid, axis=0, ddof=1).reshape(-1,1)

# Estimate predictive regression for log return based on SII
T = len(r)
#X_linear_2 = np.column_stack((np.ones(len(log_EWSI)-1), np.arange(len(log_EWSI)-1)))
X_predictive = X_predictive = sm.add_constant(SII[:-1]) 
model_predictive = sm.OLS(r[1:]*100, X_predictive)
PR_results = model_predictive.fit(cov_type='HAC', cov_kwds={'maxlags':1})
beta_hat = [PR_results.params[1], PR_results.tvalues[1]]


In [12]:
beta_hat= np.array(beta_hat).reshape(-1,1)
beta_hat = beta_hat.T

In [13]:
rho_hat = 1 / (1 + np.exp(np.mean(log_DP)))
T, GW_cols = len(log_DP), GW.shape[1]

# Create dataframes filled with NaNs
E_hat_r = pd.DataFrame(np.nan, index=np.arange(T-1), columns=np.arange(GW_cols+1))
eta_hat_DR = pd.DataFrame(np.nan, index=np.arange(T-1), columns=np.arange(GW_cols+1))
eta_hat_CF = pd.DataFrame(np.nan, index=np.arange(T-1), columns=np.arange(GW_cols+1))

beta_hat_E_hat_r = pd.DataFrame(np.nan, index=np.arange(GW_cols+1), columns=np.arange(2))
beta_hat_CF = pd.DataFrame(np.nan, index=np.arange(GW_cols+1), columns=np.arange(2))
beta_hat_DR = pd.DataFrame(np.nan, index=np.arange(GW_cols+1), columns=np.arange(2))

In [14]:
for i in range(GW_cols + 1):
    # Endogenous variables for VAR
    if i == 0:
        Y_i = np.column_stack((r, GW[:-84, 0]))
    elif i > 0 and i < GW_cols:
        Y_i = np.column_stack((r, GW[:-84, 0], GW[:-84, i]))
    elif i == GW_cols:
        Y_i = np.column_stack((r, GW[:-84, 0], PC_GW))

    Y_i_dev = Y_i - np.mean(Y_i, axis=0)
    
    A_hat_i = np.empty((Y_i.shape[1], Y_i.shape[1]))  
    A_hat_i[:] = np.NaN  # VAR slope parameters

    epsilon_hat_i = np.empty((Y_i_dev.shape[0] - 1, Y_i.shape[1]))
    epsilon_hat_i[:] = np.NaN  # VAR shocks


    for j in range(Y_i.shape[1]):
        X = Y_i_dev[:-1, :]  # Adjusted here
        y = Y_i_dev[1:, j]  # Adjusted here
        model = sm.OLS(y, X)
        results_i_j = model.fit()

        if j == 0:
            E_hat_r_i = results_i_j.fittedvalues
            E_hat_r.loc[:, i] = E_hat_r_i

        A_hat_i[j, :] = results_i_j.params
        epsilon_hat_i[:, j] = results_i_j.resid
        
    rho_hat_inv = np.linalg.inv(np.eye(Y_i.shape[1]) - rho_hat * A_hat_i)
    e1_i = np.concatenate(([1], np.zeros(Y_i.shape[1] - 1)))
    eta_hat_i = np.dot(e1_i, epsilon_hat_i.T)
    eta_hat_DR_i = np.dot(e1_i, rho_hat * A_hat_i.dot(rho_hat_inv).dot(epsilon_hat_i.T))
    eta_hat_CF_i = eta_hat_i + eta_hat_DR_i
    
    eta_hat_DR.loc[:, i] = 100 * eta_hat_DR_i
    eta_hat_CF.loc[:, i] = 100 * eta_hat_CF_i

    # Predictive regressions based on SII
    X_pred = sm.add_constant(SII[:-1])
    y_pred = 100 * (E_hat_r.values[:, i] + np.mean(r))

    model = sm.OLS(y_pred, X_pred)
    results_E_hat_r_i = model.fit(cov_type='HAC', cov_kwds={'maxlags': 1})
    
    beta_hat_E_hat_r.loc[i, :] = [results_E_hat_r_i.params[1], results_E_hat_r_i.tvalues[1]]

    y_pred = 100 * eta_hat_DR_i
    model = sm.OLS(y_pred, SII[:-1])
    results_DR_i = model.fit(cov_type='HAC', cov_kwds={'maxlags': 1})
    
    beta_hat_DR.loc[i, :] = [results_DR_i.params[0], results_DR_i.tvalues[0]]

    y_pred = 100 * eta_hat_CF_i
    model = sm.OLS(y_pred, SII[:-1])
    results_CF_i = model.fit(cov_type='HAC', cov_kwds={'maxlags': 1})

    beta_hat_CF.loc[i, :] = [results_CF_i.params[0], results_CF_i.tvalues[0]]
    
    #results_DR_i = nwest(100 * eta_hat_DR_i, SII[:-1], 1)
    #beta_hat_DR.loc[i, :] = [results_DR_i.params, results_DR_i.tvalues]
    
    #results_CF_i = nwest(100 * eta_hat_CF_i, SII[:-1], 1)
    #beta_hat_CF.loc[i, :] = [results_CF_i.params, results_CF_i.tvalues]



In [15]:
# Write results to excel file 
output_file = 'Returns_short_interest_results.xlsx'
output_sheet = 'VAR decomposition'

with pd.ExcelWriter(output_file, engine='openpyxl', mode='a',if_sheet_exists='overlay') as writer:
    pd.DataFrame(beta_hat).to_excel(writer, sheet_name=output_sheet, startrow=19, startcol=27, header=False, index=False)
    pd.DataFrame(beta_hat_E_hat_r).to_excel(writer, sheet_name=output_sheet, startrow=3, startcol=16, header=False, index=False)
    pd.DataFrame(beta_hat_CF).to_excel(writer, sheet_name=output_sheet, startrow=3, startcol=19, header=False, index=False)
    pd.DataFrame(beta_hat_DR).to_excel(writer, sheet_name=output_sheet, startrow=3, startcol=22, header=False, index=False)

In [16]:
beta_hat_CF
#beta_hat_DR
#beta_hat_E_hat_r

0         1
0  -0.211179 -1.323874
1  -0.211015 -1.318619
2  -0.241815 -1.573739
3  -0.241815 -1.573739
4  -0.154390 -1.007105
5  -0.202726 -1.338471
6  -0.310522 -1.759457
7  -0.247540 -1.498026
8  -0.228259 -1.465983
9  -0.203025 -1.286146
10 -0.225314 -1.387156
11 -0.205370 -1.228170
12 -0.204686 -1.276319
13 -0.217340 -1.351524
14 -0.230608 -1.361417
15 -0.237291 -1.494172
16 -0.258234 -1.328054
17 -0.176359 -1.295441
18 -0.163056 -1.165102